In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *
from datetime import datetime
from pyspark.sql import functions as F
from pyspark.sql.window import *

In [0]:
# dbutils.fs.ls('/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=05/')

[FileInfo(path='dbfs:/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=05/_SUCCESS', name='_SUCCESS', size=0, modificationTime=1720162202000),
 FileInfo(path='dbfs:/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=05/_committed_1001838781836836203', name='_committed_1001838781836836203', size=221, modificationTime=1720162202000),
 FileInfo(path='dbfs:/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=05/_committed_2057146281052340989', name='_committed_2057146281052340989', size=221, modificationTime=1720162144000),
 FileInfo(path='dbfs:/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=05/_committed_3706901766678831200', name='_committed_3706901766678831200', size=221, modificationTime=1720162104000),
 FileInfo(path='dbfs:/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=05/_committed_4352039372757744322', name='_committed_4352039372757744322', size=232, modificationTime=1720161657000),
 FileInfo(path='dbfs:/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=

In [0]:
# df = spark.read.format('parquet').load('/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=08/')

In [0]:
# df.printSchema()

root
 |-- BodyType: string (nullable = true)
 |-- Brand: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- ENGINE: string (nullable = true)
 |-- FuelCapacity: integer (nullable = true)
 |-- FUELTYPE: string (nullable = true)
 |-- Mileage: string (nullable = true)
 |-- Model: string (nullable = true)
 |-- MonthOfSale: string (nullable = true)
 |-- NoOfCylinders: integer (nullable = true)
 |-- Pricerange: string (nullable = true)
 |-- SeatingCapacity: integer (nullable = true)
 |-- Top_Speed: string (nullable = true)
 |-- TRANSMISSION: string (nullable = true)
 |-- YearOfSale: integer (nullable = true)



In [0]:
%sql
create schema If not exists gold;

In [0]:
def fn_top_3_cars (filepaths):
    """
    This function is used to do the Transformation on 4-wheelsdata 
    in order to findout the top_3 model cars in each Brand 

    uses Gold schema and final output saved as Delta Table
    """
    try:
        dt_string = datetime.now().strftime("year=%Y/Month=%m/day=%d")

        df = spark.read.format('parquet').load(filepaths+dt_string)

        print("select the required columns only ")

        df3 = df.select('Brand', 'Model', 'Top_Speed')

        print(f'count of df3 :: {df3.count()}')

        df4 = df3.dropDuplicates(df3.schema.names)

        print(f'count after droping duplicates :: {df4.count()}')

        w_spec = Window().partitionBy('Brand').orderBy(desc('Top_Speed'))

        df_transform = df4.withColumn('rn', row_number().over(w_spec))

        df_f = df_transform.filter(col('rn') <=3).drop('rn')

        df_f.write.mode('overwrite').format('delta').saveAsTable('gold.Top3Speed')

        print("Done")
    except Exception as e:
        raise e 


In [0]:
fn_top_3_cars(filepaths= '/mnt/genericSilver/4-WheelSales/' )

select the required columns only 
count of df3 :: 91440
count after droping duplicates :: 150
Done


In [0]:
%sql
select * from gold.top3speed;

Brand Model Top_Speed Audi RS Q8 305 Audi A8 L 250 Audi S5 Sportback 250 BMW 7 Series 310 BMW M8 305 BMW X5 300 Bentley Bentayga 290 Citroen C5 Aircross 219 Datsun Go 150 Datsun GO Plus 145 Datsun redi-GO 135 Ferrari 812 340 Ferrari F8 Tributo 340 Ferrari GTC4 Lusso 335 Honda All New City 175 Honda City 175 Honda Jazz 172 Hyundai Elantra 210 Hyundai Tucson 208 Hyundai Verna 200 Jaguar F TYPE 250 Jaguar XE 250 Jaguar XF 234 Jeep Wrangler 180 Jeep Compass 161 Kia Carnival 190 Kia Sonet 182 Kia Seltos 170 Lamborghini Huracan 325 Lamborghini Urus 305 Lexus LC 500h 250 Lexus ES 210 Lexus LX 210 MG Hector Plus 195 MG Hector 195 MG Gloster 177 MINI Cooper S 265 MINI Cooper Clubman 238 MINI Cooper Cooper Convertible 230 Mahindra Alturas G4 182 Mahindra Scorpio 163.81 Mahindra KUV100 NXT 160 Maserati Quattroporte 310 Maserati GranCabrio 301 Maserati GranTurismo 298 Mercedes Benz AMG GT 312 Mercedes Benz AMG GT 4-Door Coupe 285 Mercedes Benz AMG GLC 43 Coupe 261 Nissan GT-R 330 Nissan Kicks 165 Nissan Magnite 150 Porsche 911 330 Porsche Panamera 310 Porsche Cayenne 286 Renault Duster 170 Renault Kiger 155 Renault Triber 140 Rolls Royce Wraith 250 Rolls Royce Phantom VIII 250 Rolls Royce Dawn 250 Tata Tigor EV 80 Tata Harrier 180 Tata Nexon 180 Toyota Yaris 230 Toyota Camry 200 Toyota Fortuner 185 Volkswagen T-Roc 250 Volkswagen Tiguan AllSpace 225 Volkswagen Vento 183.8 Volvo XC90 180 kmph Volvo V90 Cross Country 180 Volvo XC40 180

In [0]:
# ## top 5 fastest cars

# df = df.withColumn('Top_Speed', col('Top_Speed').cast('int'))

# df.printSchema()

# df3 = df.select('Brand', 'Model', 'Top_Speed')

# print(f'df3 count : {df3.count()}')

# df4 = df3.dropDuplicates(df3.schema.names)
# print(f"df4 count :: {df4.count()}")

# df4.show(200, truncate=False)

# w_spec = Window().partitionBy('Brand').orderBy(desc('Top_Speed'))

# dt = df4.withColumn('rn', row_number().over(w_spec))

# df_f = dt.filter(col('rn') <=3).drop('rn')

# df_f.show(100, truncate=False)

# # df4.createOrReplaceTempView("v_test")

# df_f.write.mode('overwrite').format('delta').saveAsTable('Hemanth')

# # w_spec = Window().partitionBy(col('Brand')).orderBy(desc('Top_Speed'))

# # w_spec = Window().orderBy(col('Top_Speed').desc())

# # dt_2 = df3.withColumn('rk', row_number().over(w_spec))

# # display(dt_2)

# # display(dt_2.filter(col('rk') <=5 ).dropDuplicates(dt_2.schema.names))

root
 |-- BodyType: string (nullable = true)
 |-- Brand: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- ENGINE: string (nullable = true)
 |-- FuelCapacity: integer (nullable = true)
 |-- FUELTYPE: string (nullable = true)
 |-- Mileage: string (nullable = true)
 |-- Model: string (nullable = true)
 |-- MonthOfSale: string (nullable = true)
 |-- NoOfCylinders: integer (nullable = true)
 |-- Pricerange: string (nullable = true)
 |-- SeatingCapacity: integer (nullable = true)
 |-- Top_Speed: integer (nullable = true)
 |-- TRANSMISSION: string (nullable = true)
 |-- YearOfSale: integer (nullable = true)

df3 count : 91440
df4 count :: 150
+-------------+-----------------------+---------+
|Brand        |Model                  |Top_Speed|
+-------------+-----------------------+---------+
|BMW          |X5                     |300      |
|Hyundai      |Tucson                 |208      |
|Rolls Royce  |Cullinan               |250      |


In [0]:
## This UDF been used where in order to find out low price range of models of each Brand
def convert_to_lakhs(price):
    """
    assumes values contains "Lakh" are already in Lakhs
    crores converted to Lakhs
    1 cr = 100 Lakhs

    """
    if "Crore" in price:
        return float(price.replace(" Crore", "")) *100
    elif "Lakh" in price:
        return float(price.replace(" Lakh", ""))
    else:
        return float(price)
    

convert_to_lakhs_udf = spark.udf.register("convert_to_lakhs", convert_to_lakhs)

In [0]:
def fn_lowest_prices(filepaths):
    """
    This function is Used to findout the lowest prices of different Models 
    for each Brand

    uses the Delta Table to store the final result set 
    """
    try:
        dt_str = datetime.now().strftime("year=%Y/Month=%m/day=%d")

        df = spark.read.format('parquet').load(filepaths + dt_str)

        print("selecting only the required columns")

        df3 = df.select('Brand', 'Model', 'Pricerange')
        print(f"Count of the records without droping duplicates :: {df3.count()}")

        df4 = df3.dropDuplicates(df3.schema.names)

        print(f"Count of the unique selected records :: {df4.count()}")

        df_max_min = df4.withColumn('Low',  when(col('Pricerange').contains('-') , split(col('Pricerange'), '-')[0] ).otherwise(col('Pricerange')) )\
            .withColumn('High', when( col('Pricerange').contains('-'), split(col('Pricerange'), '-')[1] ).otherwise(col('Pricerange')))

        # display(df_max_min)

        print("Applying UDF")

        df = df_max_min.withColumn("Low2",   convert_to_lakhs_udf(col('Low')))\
                            .withColumn("High2", convert_to_lakhs_udf(col('High')))

        df_f = df.groupBy('Brand', 'Model').agg(min(col('Low2')).alias('LowestPrice_in_lakhs'))

        display(df_f)

        df_f.write.mode('overwrite').format('delta').saveAsTable('gold.LowestPrizes')

        print("Done")


    except Exception as e:
        raise e 

In [0]:
fn_lowest_prices(filepaths = '/mnt/genericSilver/4-WheelSales/' )

selecting only the required columns
Count of the records without droping duplicates :: 91440
Count of the unique selected records :: 150
Applying UDF


Brand Model LowestPrice_in_lakhs Audi A4 42.34 Audi A6 55.86 Audi A8 L 158.0 Audi Q2 34.99 Audi Q8 98.98 Audi RS Q8 206.99999999999997 Audi RS7 Sportback 194.0 Audi S5 Sportback 79.06 BMW 2 Series Gran Coupe 37.9 BMW 3 Series 42.6 BMW 3 Series Gran Limousine 51.5 BMW 5 Series 56.0 BMW 6 Series GT 67.9 BMW 7 Series 1.38 BMW 8 Series 1.33 BMW M2 85.0 BMW M5 155.0 BMW M8 218.00000000000003 BMW X1 37.2 BMW X3 56.5 BMW X3 M 99.9 BMW X4 62.4 BMW X5 75.5 BMW X5 M 195.0 BMW X6 96.9 BMW X7 93.0 BMW Z4 67.0 Bentley Bentayga 409.99999999999994 Citroen C5 Aircross 29.9 Datsun GO Plus 4.26 Datsun Go 4.03 Datsun redi-GO 3.84 Ferrari 812 520.0 Ferrari F8 Tributo 401.99999999999994 Ferrari GTC4 Lusso 4.23 Ferrari Portofino 350.0 Honda All New City 11.02 Honda Amaze 6.24 Honda City 9.3 Honda Jazz 7.63 Honda WR-V 8.7 Hyundai Aura 5.92 Hyundai Creta 10.0 Hyundai Elantra 17.83 Hyundai Grand i10 Nios 5.19 Hyundai Kona Electric 24.15 Hyundai Santro 4.67 Hyundai Tucson 22.55 Hyundai Venue 6.87 Hyundai Verna 9.11 Hyundai i20 6.8 Jaguar F TYPE 95.12 Jaguar F-Pace 66.07 Jaguar I-Pace 1.06 Jaguar XE 46.64 Jaguar XF 55.67 Jeep Compass 16.99 Jeep Wrangler 53.9 Kia Carnival 24.95 Kia Seltos 9.89 Kia Sonet 6.79 Lamborghini Huracan 3.22 Lamborghini Urus 310.0 Lexus ES 56.55 Lexus LC 500h 2.1 Lexus LS 1.91 Lexus LX 233.0 Lexus NX 58.2 Lexus RX 104.0 MG Gloster 29.98 MG Hector 13.18 MG Hector Plus 13.63 MG ZS EV 21.0 MINI Cooper Clubman 41.9 MINI Cooper Cooper Convertible 40.01 MINI Cooper Countryman 39.5 MINI Cooper S 35.06 Mahindra Alturas G4 28.73 Mahindra Bolero 8.12 Mahindra KUV100 NXT 5.87 Mahindra Marazzo 11.64 Mahindra Scorpio 11.98 Mahindra Thar 10.0 Mahindra XUV300 7.95 Mahindra XUV500 13.8 Maserati Ghibli 1.15 Maserati GranCabrio 268.0 Maserati GranTurismo 225.0 Maserati Levante 145.0 Maserati Quattroporte 1.64 Mercedes Benz A-Class Limousine 39.9 Mercedes Benz AMG GLC 43 Coupe 81.22 Mercedes Benz AMG GLE Coupe 127.0 Mercedes Benz AMG GT 248.0 Mercedes Benz AMG GT 4-Door Coupe 242.0 Mercedes Benz C Class 49.41 Mercedes Benz C Coupe 79.93 Mercedes Benz CLS 86.39 Mercedes Benz E Class 63.6 Mercedes Benz E-Class All-Terrain 77.25 Mercedes Benz EQC 104.0 Mercedes Benz G Class 1.62 Mercedes Benz GLC Class 57.36 Mercedes Benz GLC Coupe 66.66 Mercedes Benz GLE 77.25 Mercedes Benz GLS 105.0 Mercedes Benz S Class 1.42 Mercedes Benz V-Class 71.1 Nissan GT-R 212.0 Nissan Kicks 9.5 Nissan Magnite 5.59 Porsche 718 85.46 Porsche 911 1.64 Porsche Cayenne 1.2 Porsche Cayenne Coupe 1.32 Porsche Macan 69.98 Porsche Panamera 1.44 Renault Duster 9.73 Renault Kiger 5.45 Renault Kwid 3.18 Renault Triber 5.29 Rolls Royce Cullinan 695.0 Rolls Royce Dawn 592.0 Rolls Royce Phantom VIII 950.0 Rolls Royce Wraith 500.0 Tata Altroz 5.7 Tata Harrier 14.0 Tata Nexon 7.1 Tata Nexon EV 13.99 Tata Safari 14.69 Tata Tiago 4.86 Tata Tigor 5.5 Tata Tigor EV 10.51 Toyota Camry 40.59 Toyota Fortuner 30.34 Toyota Glanza 7.18 Toyota Innova Crysta 16.52 Toyota Urban Cruiser 8.5 Toyota Vellfire 87.0 Toyota Yaris 9.16 Volkswagen Polo 6.17 Volkswagen T-Roc 21.35 Volkswagen Tiguan AllSpace 34.2 Volkswagen Vento 9.14 Volvo S60 45.9 Volvo S90 59.0 Volvo V90 Cross Country 65.41 Volvo XC40 39.9 Volvo XC60 59.9 Volvo XC90 80.99

Done


In [0]:
# df = spark.read.format('parquet').load('/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=08/')

In [0]:
# df.printSchema()

root
 |-- BodyType: string (nullable = true)
 |-- Brand: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- ENGINE: string (nullable = true)
 |-- FuelCapacity: integer (nullable = true)
 |-- FUELTYPE: string (nullable = true)
 |-- Mileage: string (nullable = true)
 |-- Model: string (nullable = true)
 |-- MonthOfSale: string (nullable = true)
 |-- NoOfCylinders: integer (nullable = true)
 |-- Pricerange: string (nullable = true)
 |-- SeatingCapacity: integer (nullable = true)
 |-- Top_Speed: string (nullable = true)
 |-- TRANSMISSION: string (nullable = true)
 |-- YearOfSale: integer (nullable = true)



In [0]:
# df_selected = df.select('Pricerange', 'Brand', 'Model')

# df4 = df_selected.dropDuplicates(df_selected.schema.names)

# df4.show(10, truncate=False)

+-----------------------+-------+-------------+
|Pricerange             |Brand  |Model        |
+-----------------------+-------+-------------+
|85.46 Lakh - 1.64 Crore|Porsche|718          |
|1.2 - 1.93 Crore       |Porsche|Cayenne      |
|55.86 - 60.51 Lakh     |Audi   |A6           |
|1.58 Crore             |Audi   |A8 L         |
|1.94 Crore             |Audi   |RS7 Sportback|
|69.98 - 85.01 Lakh     |Porsche|Macan        |
|1.64 - 3.08 Crore      |Porsche|911          |
|34.99 - 48.89 Lakh     |Audi   |Q2           |
|98.98 Lakh - 1.35 Crore|Audi   |Q8           |
|42.34 - 46.67 Lakh     |Audi   |A4           |
+-----------------------+-------+-------------+
only showing top 10 rows



In [0]:
# df_max_min = df4.withColumn('Low', when(col('Pricerange').contains('-') , split(col('Pricerange'), '-')[0] ).otherwise(col('Pricerange')))\
#             .withColumn('High',  when(col('Pricerange').contains('-'), split(col('Pricerange'), '-')[1]).otherwise(col('Pricerange')) )




# def convert_to_lakhs(price):
#     """
#     assumes values contains "Lakh" are already in Lakhs
#     crores converted to Lakhs
#     1 cr = 100 Lakhs

#     """
#     if "Crore" in price:
#         return float(price.replace(" Crore", "")) *100
#     elif "Lakh" in price:
#         return float(price.replace(" Lakh", ""))
#     else:
#         return float(price)
    

# convert_to_lakhs_udf = spark.udf.register("convert_to_lakhs", convert_to_lakhs)

In [0]:
# # df = df_max_min.withColumn("Low2", when(col("Low").rlike("Crore|Lakh"), convert_to_lakhs_udf(col("Low"))).otherwise(col("Low"))) \
# #     .withColumn("Low2", trim(col("Low2"))).show()

# df = df_max_min.withColumn("Low2",   convert_to_lakhs_udf(col('Low')))\
#     .withColumn("High2", convert_to_lakhs_udf(col('High')))

# df.show(20, truncate=False)

# df_f = df.groupBy('Brand', 'Model').agg(min(col('Low2')).alias('LowestPrice_in_lakhs'))

# df_f.show(10, truncate=False)

+-----------------------+-------------+-----------------------+-----------+-----------+------------------+------------------+
|Pricerange             |Brand        |Model                  |Low        |High       |Low2              |High2             |
+-----------------------+-------------+-----------------------+-----------+-----------+------------------+------------------+
|40.01 Lakh             |MINI Cooper  |Cooper Convertible     |40.01 Lakh |40.01 Lakh |40.01             |40.01             |
|7.95 - 12.55 Lakh      |Mahindra     |XUV300                 |7.95       | 12.55 Lakh|7.95              |12.55             |
|4.02 Crore             |Ferrari      |F8 Tributo             |4.02 Crore |4.02 Crore |401.99999999999994|401.99999999999994|
|5.92 - 9.32 Lakh       |Hyundai      |Aura                   |5.92       | 9.32 Lakh |5.92              |9.32              |
|85.46 Lakh - 1.64 Crore|Porsche      |718                    |85.46 Lakh | 1.64 Crore|85.46             |164.0       

In [0]:
# df_max_min.show(200,truncate=False)

+-----------------------+-------------+-----------------------+-----------+-----------+
|Pricerange             |Brand        |Model                  |Low        |High       |
+-----------------------+-------------+-----------------------+-----------+-----------+
|40.01 Lakh             |MINI Cooper  |Cooper Convertible     |40.01 Lakh |40.01 Lakh |
|7.95 - 12.55 Lakh      |Mahindra     |XUV300                 |7.95       | 12.55 Lakh|
|4.02 Crore             |Ferrari      |F8 Tributo             |4.02 Crore |4.02 Crore |
|5.92 - 9.32 Lakh       |Hyundai      |Aura                   |5.92       | 9.32 Lakh |
|85.46 Lakh - 1.64 Crore|Porsche      |718                    |85.46 Lakh | 1.64 Crore|
|6.24 - 9.99 Lakh       |Honda        |Amaze                  |6.24       | 9.99 Lakh |
|51.5 - 53.9 Lakh       |BMW          |3 Series Gran Limousine|51.5       | 53.9 Lakh |
|5.5 - 7.64 Lakh        |Tata         |Tigor                  |5.5        | 7.64 Lakh |
|5.87 - 7.45 Lakh       |Mahindr

In [0]:

# df_price.select('Low').show(200, truncate=False)

+-----------+
|Low        |
+-----------+
|4000999.8  |
|7.95       |
|4.02E7     |
|5.92       |
|8546000.0  |
|6.24       |
|51.5       |
|5.5        |
|5.87       |
|11.02      |
|6.17       |
|10.51      |
|6607000.0  |
|8.7        |
|9.3        |
|29.9       |
|1.2        |
|1.55E7     |
|10.0       |
|1.27E7     |
|56.0       |
|42.6       |
|6.8        |
|10.0       |
|1.15       |
|39.5       |
|55.86      |
|4590000.0  |
|4.67       |
|13.63      |
|1.58E7     |
|9512000.0  |
|9.16       |
|2.42E7     |
|8.12       |
|62.4       |
|63.6       |
|2.33E7     |
|56.55      |
|1.04E7     |
|9.14       |
|1.94E7     |
|5.92E7     |
|69.98      |
|37.2       |
|5900000.0  |
|8099000.0  |
|1.95E7     |
|8.5        |
|11.64      |
|7.18       |
|21.0       |
|30.34      |
|49.41      |
|1.91       |
|22.55      |
|1.64       |
|2135000.0  |
|11.98      |
|37.9       |
|58.2       |
|13.18      |
|7725000.0  |
|1.05E7     |
|6.79       |
|34.99      |
|9.11       |
|1.04E7     |
|35.06

In [0]:
# df_t = df4.withColumn('minprice', extract_min_price_udf(col('Pricerange'))).show()

+--------------------+-------------+-------------------+--------+
|          Pricerange|        Brand|              Model|minprice|
+--------------------+-------------+-------------------+--------+
|85.46 Lakh - 1.64...|      Porsche|                718|    NULL|
|    1.2 - 1.93 Crore|      Porsche|            Cayenne|    NULL|
|          1.27 Crore|Mercedes Benz|      AMG GLE Coupe|    NULL|
|  55.86 - 60.51 Lakh|         Audi|                 A6|    NULL|
|          1.58 Crore|         Audi|               A8 L|    NULL|
|          2.42 Crore|Mercedes Benz|AMG GT 4-Door Coupe|    NULL|
|    63.6 - 80.9 Lakh|Mercedes Benz|            E Class|    NULL|
|          1.94 Crore|         Audi|      RS7 Sportback|    NULL|
|  69.98 - 85.01 Lakh|      Porsche|              Macan|    NULL|
|  49.41 - 65.55 Lakh|Mercedes Benz|            C Class|    NULL|
|   1.64 - 3.08 Crore|      Porsche|                911|    NULL|
|          77.25 Lakh|Mercedes Benz|E-Class All-Terrain|    NULL|
|         

In [0]:
%sql
-- select * from hemanth

Brand Model Top_Speed Audi RS Q8 305 Audi A6 250 Audi A8 L 250 BMW 7 Series 310 BMW M8 305 BMW X5 300 Bentley Bentayga 290 Citroen C5 Aircross 219 Datsun Go 150 Datsun GO Plus 145 Datsun redi-GO 135 Ferrari 812 340 Ferrari F8 Tributo 340 Ferrari GTC4 Lusso 335 Honda City 175 Honda All New City 175 Honda Jazz 172 Hyundai Elantra 210 Hyundai Tucson 208 Hyundai Verna 200 Jaguar XE 250 Jaguar F TYPE 250 Jaguar XF 234 Jeep Wrangler 180 Jeep Compass 161 Kia Carnival 190 Kia Sonet 182 Kia Seltos 170 Lamborghini Huracan 325 Lamborghini Urus 305 Lexus LC 500h 250 Lexus LX 210 Lexus ES 210 MG Hector 195 MG Hector Plus 195 MG Gloster 177 MINI Cooper S 265 MINI Cooper Clubman 238 MINI Cooper Cooper Convertible 230 Mahindra Alturas G4 182 Mahindra Scorpio 163 Mahindra KUV100 NXT 160 Maserati Quattroporte 310 Maserati GranCabrio 301 Maserati GranTurismo 298 Mercedes Benz AMG GT 312 Mercedes Benz AMG GT 4-Door Coupe 285 Mercedes Benz AMG GLC 43 Coupe 261 Nissan GT-R 330 Nissan Kicks 165 Nissan Magnite 150 Porsche 911 330 Porsche Panamera 310 Porsche Cayenne 286 Renault Duster 170 Renault Kiger 155 Renault Triber 140 Rolls Royce Cullinan 250 Rolls Royce Phantom VIII 250 Rolls Royce Dawn 250 Tata Harrier 180 Tata Nexon 180 Tata Safari 175 Toyota Yaris 230 Toyota Camry 200 Toyota Fortuner 185 Volkswagen T-Roc 250 Volkswagen Tiguan AllSpace 225 Volkswagen Vento 183 Volvo XC60 180 Volvo V90 Cross Country 180 Volvo S60 180

In [0]:
%sql
-- select * from default.hemanth order by Top_Speed desc limit 5;

-- select * , row_number() over (partition by Brand order by Top_Speed desc) as lokie from default.hemanth ;

select distinct Brand ,Model,Top_Speed ,row_number() over (order by Top_Speed, Brand desc) as lokie from default.hemanth ;

Brand Model Top_Speed lokie Volvo XC90 null 1 Tata Tigor EV 80 2 Tata Altroz 100 3 BMW X6 100 4 Mahindra Bolero 117 5 Tata Nexon EV 120 6 Renault Kwid 135 7 Datsun redi-GO 135 8 Renault Triber 140 9 MG ZS EV 140 10 Honda WR-V 140 11 Mahindra XUV500 144 12 Mahindra Marazzo 145 13 Datsun GO Plus 145 14 Tata Tiago 150 15 Nissan Magnite 150 16 Datsun Go 150 17 Renault Kiger 155 18 Mahindra Thar 155 19 Hyundai Aura 155 20 Hyundai Kona Electric 155 21 Hyundai Santro 156 22 Mahindra KUV100 NXT 160 23 Mahindra XUV300 160 24 Hyundai Grand i10 Nios 160 25 Hyundai Venue 160 26 Honda Amaze 160 27 Jeep Compass 161 28 Mahindra Scorpio 163 29 Volkswagen Polo 164 30 Tata Tigor 164 31 Nissan Kicks 165 32 Hyundai Creta 165 33 Hyundai i20 167 34 Toyota Vellfire 170 35 Toyota Urban Cruiser 170 36 Renault Duster 170 37 Kia Seltos 170 38 Honda Jazz 172 39 Tata Safari 175 40 Honda City 175 41 Honda All New City 175 42 MG Gloster 177 43 Toyota Innova Crysta 179 44 Volvo XC60 180 45 Volvo V90 Cross Country 180 46 Volvo S60 180 47 Volvo S90 180 48 Volvo XC40 180 49 Toyota Glanza 180 50 Tata Harrier 180 51 Tata Nexon 180 52 Mercedes Benz EQC 180 53 Lexus NX 180 54 Jeep Wrangler 180 55 Mahindra Alturas G4 182 56 Kia Sonet 182 57 Volkswagen Vento 183 58 Toyota Fortuner 185 59 Kia Carnival 190 60 Mercedes Benz V-Class 195 61 MG Hector 195 62 MG Hector Plus 195 63 Toyota Camry 200 64 Lexus RX 200 65 Jaguar I-Pace 200 66 Hyundai Verna 200 67 Lexus LS 205 68 Hyundai Tucson 208 69 Mercedes Benz G Class 210 70 Lexus LX 210 71 Lexus ES 210 72 Hyundai Elantra 210 73 BMW X3 213 74 Jaguar F-Pace 217 75 Citroen C5 Aircross 219 76 Mercedes Benz GLC Coupe 220 77 Mercedes Benz GLS 222 78 BMW X1 222 79 Volkswagen Tiguan AllSpace 225 80 Mercedes Benz GLE 225 81 Mercedes Benz AMG GLE Coupe 225 82 MINI Cooper Countryman 225 83 BMW X7 227 84 Audi Q2 228 85 Toyota Yaris 230 86 MINI Cooper Cooper Convertible 230 87 Mercedes Benz E-Class All-Terrain 231 88 Mercedes Benz E Class 231 89 BMW 2 Series Gran Coupe 233 90 Jaguar XF 234 91 BMW X4 235 92 MINI Cooper Clubman 238 93 Mercedes Benz C Class 240 94 Mercedes Benz GLC Class 240 95 Audi A4 241 96 Volkswagen T-Roc 250 97 Rolls Royce Cullinan 250 98 Rolls Royce Phantom VIII 250 99 Rolls Royce Dawn 250 100 Rolls Royce Wraith 250 101 Mercedes Benz C Coupe 250 102 Mercedes Benz A-Class Limousine 250 103 Mercedes Benz CLS 250 104 Mercedes Benz S Class 250 105 Lexus LC 500h 250 106 Jaguar XE 250 107 Jaguar F TYPE 250 108 BMW Z4 250 109 BMW 5 Series 250 110 BMW X5 M 250 111 BMW M5 250 112 BMW 3 Series 250 113 BMW M2 250 114 BMW 6 Series GT 250 115 BMW 3 Series Gran Limousine 250 116 Audi A6 250 117 Audi A8 L 250 118 Audi S5 Sportback 250 119 Audi RS7 Sportback 250 120 Audi Q8 250 121 Porsche Macan 254 122 BMW 8 Series 258 123 Mercedes Benz AMG GLC 43 Coupe 261 124 Maserati Levante 264 125 MINI Cooper S 265 126 Porsche 718 275 127 BMW X3 M 280 128 Mercedes Benz AMG GT 4-Door Coupe 285 129 Porsche Cayenne 286 130 Porsche Cayenne Coupe 286 131 Maserati Ghibli 286 132 Bentley Bentayga 290 133 Maserati GranTurismo 298 134 BMW X5 300 135 Maserati GranCabrio 301 136 Lamborghini Urus 305 137 BMW M8 305 138 Audi RS Q8 305 139 Porsche Panamera 310 140 Maserati Quattroporte 310 141 BMW 7 Series 310 142 Mercedes Benz AMG GT 312 143 Ferrari Portofino 320 144 Lamborghini Huracan 325 145 Porsche 911 330 146 Nissan GT-R 330 147 Ferrari GTC4 Lusso 335 148 Ferrari 812 340 149 Ferrari F8 Tributo 340 150

In [0]:
# %sql
# create schema If not exists gold

In [0]:
def pharse_mileage(filepath):
    """
    This Method is usually converts the Mileage column from string to int and
    also split the values like High and Low 
    ex : 9-40 kmpl >> 9 , 40 

    Transform the avg_low_mileage and avg_high_mileage for each Brand
    """
    try:
        dt_string = datetime.now().strftime("year=%Y/Month=%m/day=%d")
        df = spark.read.format('parquet').load(filepath+dt_string)

        df.printSchema()

        df = df.withColumn('Low', when(col('Mileage').contains('-') , split(col('Mileage'), '-')[0] ).otherwise(0))\
            .withColumn('High',  when(col('Mileage').contains('-'), split(col('Mileage'), '-')[1]).otherwise(col('Mileage')) )


        df = df.withColumn('High', regexp_replace(df['High'], 'kmpl', '').cast('int'))
        
        df2 = df.withColumn('Low', regexp_replace(df['Low'], 'kmpl', '').cast('int'))

        display(df2)

        print("new schema")
        df2.printSchema()

        df_tr = df2.groupBy(df2['Brand']).agg(round(avg('Low'),2).alias('Avg_Low_values'), round(avg('High'),2).alias('High_Low_Values'))

        display(df_tr)

        df_tr.write.mode('overwrite').format('delta').saveAsTable('gold.Mileage')

        print("Done")

        

    except Exception as e:
        raise e 

In [0]:
pharse_mileage(filepath='/mnt/genericSilver/4-WheelSales/')

root
 |-- BodyType: string (nullable = true)
 |-- Brand: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- ENGINE: string (nullable = true)
 |-- FuelCapacity: integer (nullable = true)
 |-- FUELTYPE: string (nullable = true)
 |-- Mileage: string (nullable = true)
 |-- Model: string (nullable = true)
 |-- MonthOfSale: string (nullable = true)
 |-- NoOfCylinders: integer (nullable = true)
 |-- Pricerange: string (nullable = true)
 |-- SeatingCapacity: integer (nullable = true)
 |-- Top_Speed: string (nullable = true)
 |-- TRANSMISSION: string (nullable = true)
 |-- YearOfSale: integer (nullable = true)



BodyType Brand City Country ENGINE FuelCapacity FUELTYPE Mileage Model MonthOfSale NoOfCylinders Pricerange SeatingCapacity Top_Speed TRANSMISSION YearOfSale Low High SUV Porsche Hyderabad India 1984 to 2995 cc 75 Petrol 14 kmpl Macan January 6 69.98 - 85.01 Lakh 5 254 Automatic 2017 0 14 Coupe Porsche Hyderabad India 1988 to 3995 cc 54 Petrol 9 kmpl 718 April 8 85.46 Lakh - 1.64 Crore 2 275 Automatic 2017 0 9 Coupe Porsche Hyderabad India 1988 to 3995 cc 54 Petrol 9 kmpl 718 April 8 85.46 Lakh - 1.64 Crore 2 275 Manual 2017 0 9 SUV Porsche Hyderabad India 2995 to 3996 cc 75 Petrol 9 - 40 kmpl Cayenne January 6 1.2 - 1.93 Crore 5 286 Automatic 2017 9 40 Coupe Porsche Hyderabad India 2995 to 3996 cc 75 Petrol 10.75 kmpl Cayenne Coupe January 8 1.32 - 1.98 Crore 4 286 Automatic 2017 0 10 Sedan Porsche Hyderabad India 2894 to 4806 cc 75 Petrol 8-37 kmpl Panamera January 6 1.44 - 2.43 Crore 4 310 Automatic 2017 8 37 Coupe Porsche Hyderabad India 2981 to 3745 cc 64 Petrol 9 - 12 kmpl 911 January 8 1.64 - 3.08 Crore 4 330 Automatic 2017 9 12 Coupe Porsche Hyderabad India 2981 to 3745 cc 64 Petrol 9 - 12 kmpl 911 January 8 1.64 - 3.08 Crore 4 330 Manual 2017 9 12 SUV Porsche Hyderabad India 1984 to 2995 cc 75 Petrol 14 kmpl Macan February 6 69.98 - 85.01 Lakh 5 254 Automatic 2017 0 14 Coupe Porsche Hyderabad India 1988 to 3995 cc 54 Petrol 9 kmpl 718 April 8 85.46 Lakh - 1.64 Crore 2 275 Automatic 2018 0 9 Coupe Porsche Hyderabad India 1988 to 3995 cc 54 Petrol 9 kmpl 718 April 8 85.46 Lakh - 1.64 Crore 2 275 Manual 2018 0 9 SUV Porsche Hyderabad India 2995 to 3996 cc 75 Petrol 9 - 40 kmpl Cayenne February 6 1.2 - 1.93 Crore 5 286 Automatic 2017 9 40 Coupe Porsche Hyderabad India 2995 to 3996 cc 75 Petrol 10.75 kmpl Cayenne Coupe February 8 1.32 - 1.98 Crore 4 286 Automatic 2017 0 10 Sedan Porsche Hyderabad India 2894 to 4806 cc 75 Petrol 8-37 kmpl Panamera February 6 1.44 - 2.43 Crore 4 310 Automatic 2017 8 37 Coupe Porsche Hyderabad India 2981 to 3745 cc 64 Petrol 9 - 12 kmpl 911 February 8 1.64 - 3.08 Crore 4 330 Automatic 2017 9 12 Coupe Porsche Hyderabad India 2981 to 3745 cc 64 Petrol 9 - 12 kmpl 911 February 8 1.64 - 3.08 Crore 4 330 Manual 2017 9 12 SUV Porsche Hyderabad India 1984 to 2995 cc 75 Petrol 14 kmpl Macan March 6 69.98 - 85.01 Lakh 5 254 Automatic 2017 0 14 Coupe Porsche Hyderabad India 1988 to 3995 cc 54 Petrol 9 kmpl 718 April 8 85.46 Lakh - 1.64 Crore 2 275 Automatic 2019 0 9 Coupe Porsche Hyderabad India 1988 to 3995 cc 54 Petrol 9 kmpl 718 April 8 85.46 Lakh - 1.64 Crore 2 275 Manual 2019 0 9 SUV Porsche Hyderabad India 2995 to 3996 cc 75 Petrol 9 - 40 kmpl Cayenne March 6 1.2 - 1.93 Crore 5 286 Automatic 2017 9 40 Coupe Porsche Hyderabad India 2995 to 3996 cc 75 Petrol 10.75 kmpl Cayenne Coupe March 8 1.32 - 1.98 Crore 4 286 Automatic 2017 0 10 Sedan Porsche Hyderabad India 2894 to 4806 cc 75 Petrol 8-37 kmpl Panamera March 6 1.44 - 2.43 Crore 4 310 Automatic 2017 8 37 Coupe Porsche Hyderabad India 2981 to 3745 cc 64 Petrol 9 - 12 kmpl 911 March 8 1.64 - 3.08 Crore 4 330 Automatic 2017 9 12 Coupe Porsche Hyderabad India 2981 to 3745 cc 64 Petrol 9 - 12 kmpl 911 March 8 1.64 - 3.08 Crore 4 330 Manual 2017 9 12 SUV Porsche Hyderabad India 1984 to 2995 cc 75 Petrol 14 kmpl Macan April 6 69.98 - 85.01 Lakh 5 254 Automatic 2017 0 14 Coupe Porsche Mumbai India 1988 to 3995 cc 54 Petrol 9 kmpl 718 April 8 85.46 Lakh - 1.64 Crore 2 275 Automatic 2017 0 9 Coupe Porsche Mumbai India 1988 to 3995 cc 54 Petrol 9 kmpl 718 April 8 85.46 Lakh - 1.64 Crore 2 275 Manual 2017 0 9 SUV Porsche Hyderabad India 2995 to 3996 cc 75 Petrol 9 - 40 kmpl Cayenne April 6 1.2 - 1.93 Crore 5 286 Automatic 2017 9 40 Coupe Porsche Hyderabad India 2995 to 3996 cc 75 Petrol 10.75 kmpl Cayenne Coupe April 8 1.32 - 1.98 Crore 4 286 Automatic 2017 0 10 Sedan Porsche Hyderabad India 2894 to 4806 cc 75 Petrol 8-37 kmpl Panamera April 6 1.44 - 2.43 Crore 4 310 Automatic 2017 8 37 Coupe Porsche Hyderabad India 2981 to 3745 cc 64 Petrol 9 - 12 kmpl 91

new schema
root
 |-- BodyType: string (nullable = true)
 |-- Brand: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- ENGINE: string (nullable = true)
 |-- FuelCapacity: integer (nullable = true)
 |-- FUELTYPE: string (nullable = true)
 |-- Mileage: string (nullable = true)
 |-- Model: string (nullable = true)
 |-- MonthOfSale: string (nullable = true)
 |-- NoOfCylinders: integer (nullable = true)
 |-- Pricerange: string (nullable = true)
 |-- SeatingCapacity: integer (nullable = true)
 |-- Top_Speed: string (nullable = true)
 |-- TRANSMISSION: string (nullable = true)
 |-- YearOfSale: integer (nullable = true)
 |-- Low: integer (nullable = true)
 |-- High: integer (nullable = true)



Brand Avg_Low_values High_Low_Values Volkswagen 10.67 18.0 Lexus 0.0 13.17 Jaguar 1.6 12.75 Maserati 2.57 14.57 Tata 8.63 21.14 Jeep 11.2 15.6 Kia 15.11 21.11 Volvo 0.0 15.57 Hyundai 17.15 23.06 Honda 13.23 22.54 Audi 0.0 12.13 Lamborghini 0.0 9.5 MINI Cooper 4.0 16.25 Rolls Royce 1.5 8.0 Renault 13.75 18.25 Mahindra 5.2 16.47 BMW 7.47 17.37 MG 9.5 15.86 Datsun 19.67 20.67 Ferrari 0.0 10.5 Porsche 4.38 17.88 Citroen 0.0 18.0 Bentley 0.0 8.0 Mercedes Benz 4.22 13.07 Toyota 11.13 16.31 Nissan 12.8 16.4

Done


In [0]:

# df = spark.read.format('parquet').load('/mnt/genericSilver/4-WheelSales/year=2024/Month=07/day=05/')

# df2 = df.select(F.col('Mileage')).withColumn('Low', when(F.col('Mileage').contains('-'), split(F.col('Mileage'), '-')[0]).otherwise(0))\
#         .withColumn('High', when(F.col('Mileage').contains('-'), split(F.col('Mileage'), '-')[1]).otherwise(F.col('Mileage')))

# df3 = df2.withColumn('High', F.regexp_replace(F.col('High'), 'kmpl', '').cast('int'))\
#     .withColumn('Low', F.regexp_replace(F.col('Low'), 'kmpl', '').cast('int'))

# display(df3)

# df3.printSchema()


Mileage Low High 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 kmpl 0 14 9 kmpl 0 9 9 kmpl 0 9 9 - 40 kmpl 9 40 10.75 kmpl 0 10 8-37 kmpl 8 37 9 - 12 kmpl 9 12 9 - 12 kmpl 9 12 14 km

root
 |-- Mileage: string (nullable = true)
 |-- Low: integer (nullable = true)
 |-- High: integer (nullable = true)



In [0]:
# %sql

# select * from gold.mileage

Brand Avg_Low_values High_Low_Values Volkswagen 10.67 18.0 Lexus 0.0 13.17 Jaguar 1.6 12.75 Maserati 2.57 14.57 Tata 8.63 21.14 Jeep 11.2 15.6 Kia 15.11 21.11 Volvo 0.0 15.57 Hyundai 17.15 23.06 Honda 13.23 22.54 Audi 0.0 12.13 Lamborghini 0.0 9.5 MINI Cooper 4.0 16.25 Rolls Royce 1.5 8.0 Renault 13.75 18.25 Mahindra 5.2 16.47 BMW 7.47 17.37 MG 9.5 15.86 Datsun 19.67 20.67 Ferrari 0.0 10.5 Porsche 4.38 17.88 Citroen 0.0 18.0 Bentley 0.0 8.0 Mercedes Benz 4.22 13.07 Toyota 11.13 16.31 Nissan 12.8 16.4